## Study on BERT Tensorflow implementation and application

**BERT** is a huge contribution to the NLP community by Google Research.  Here I would like to learn all I can from BERT, specifically its TensorFlow implementation and applications.


BERT, which stands for Bidirectional  Encoder Representations from Transformers.  Probably a little playfulness there in acronym, considering a few months ago before BERT, Allen Institute AI research team released ELmo -- a new deep contextual word embeddings. 

BERT is a language representation in the sense it not only captures the word meanings in a context by its Cloze Task training, and by the NSP(next sentence prediction) training it also understands meanings at sentence level, and even captures some common sense knowledge because the next sentence has to be logically coherently to the previous.  

Transfer learning shows the importance of pretrained models.  There are two ways to do transfer learning in this NLP context, features based and fine tuning based.  BERT can be used in both ways, but fine tuning seems to be more superior.  

BERT uses Transformers (layered multiheaded attentions architecure) on big corpus like BooksCorpus (800M words) and English Wikipedia (2,500M words), trained on two tasks (Cloze task and NSP task). It is said to be unsupervised learning, but really it is supervised. In a sense, human thinking logic and world knowledge embedded in a language is the ground truth, so training on big datasets is crucial because only a big enough dataset can properly represent all the human thinking and world knowledge and only then it is poissble to reduce them into a language representation model described by hunreds of millions of parameters.

A word on Transformer architecture, it is a beautiful design. The multilayered multiheaded attention mechanism, very much like a convolution operation with multiple filters(kernels), it extracts language patterns from sub word level to word to phrase and to sentence and between sentences. I think it is what gives BERT the power it possesses. Also the residual connection resembles the same in ResNet, which makes deeper layered design possible and more powerful.



### BERT architecture notes:

* Tokenization: 
   * use WordPiece to tokenize the text, which is a commonly used way to handle rare/OOV words effectively. (main idea: use sub-words (word piece) to represent words, which will be able to find something for OOV or rare words, so they can be represented in a way).  BERT uses a 30k vocabulary.

* Embeddings:  Three types: token(wordpiece) embedding, segement embedding and token position embedding.
  trainable parameters: token embedding: 30522*768,  segment embedding: 2*768 (no need to learn, use one-hot encoding), position embedding:  512*768 
* Transformer architecture:
    * What is attention: "An attention function can be described as mapping a query and a set of key-value pairs to an output, where the query, keys, values, and output are all vectors. The output is computed as a weighted sum of the values, where the weight assigned to each value is computed by a compatibility function of the query with the corresponding key." Where the compatibility function used here is dot product.
    * Transformer uses residual layer to ensure the gradient can propergate throughout layers so deeper layered structure is valid, so we can use more layers to discover more hidden patterns.
    * there is a feed forward layer used gelu (Gaussian Error Linear Units):  
        * GELU(x) = xP(X ≤ x) = xΦ(x).
        * and proximated as 0.5x(1 + tanh[sqrt(2/π)(x + 0.044715x^3)])  
* main design ideas:  Cloze(Masking out words) Task  training and Next Sentense Prediction Task (a text entailing task). These ideas bring the BERT model its power as a good language representation, extracting the meaning of words in context, semantics in a sentence and common-sense knowledge in a language.

* Transfer learning strategy used in BERT: pretrain a model, then apply to target task via fine tuning strategy, it can also be used as feature-based for downstream tasks.   

   

### Types of common sense knowledges (something may be studied for BERT model?)
https://www.aclweb.org/anthology/P11-2057


        Category Occurrences κ 
        
        Functionality 19.2 (8.7%) 0.663
        Definitions 17.2 (7.8%) 0.633
        Preconditions 15.8 (7.1%) 0.775
        Cause and Effect 10.8 (4.9%) 0.591
        Prominent Relationship 8.4 (3.8%) 0.145
        Argument Types 6.8 (3.1%) 0.180
        Simultaneous Conditions 6.2 (2.8%) 0.203
        Mutual Exclusivity 6 (2.7%) 0.640
        Transitivity 3 (1.4%) 0.459
        Geography 36.4 (16.5%) 0.927
        Support/Opposition 14.6 (6.6%) 0.684
        Arithmetic 13.4 (6.1%) 0.968
        is member of 11.6 (5.2%) 0.663
        Synecdoche 9.8 (4.4%) 0.829
        has parts 8.8 (4.0%) 0.882
        Accountability 7.2 (3.3%) 0.799
        Cultural/Situational 4.6 (2.1%) 0.267
        Public Entities 3.2 (1.4%) 0.429
        Omniscience 7.2 (3.3%) 0.828
        Probabilistic Dependency 4.8 (2.2%) 0.297
        
        All 215 (97%) 0.678
        
        Frequency and inter-annotator agreement for each category of world knowledge in the survey. Frequencies are averaged over the five annotators, and agreement is calculated using Fleiss’s κ.

###  Steps to pre-train a BERT model:
1. segment data into one sentence per line and separate documents by empty lines.
2. run create_pretrain_data.py with approporiate arguments: (the following are my testing setup)
    * --input_file=./sample_text.txt   
    * --output_file=./tmp/tf_examples.tfrecord   
    * --vocab_file=./pretrained/uncased_L-12_H-768_A-12/vocab.txt   
    * --do_lower_case=True   
    * --max_seq_length=128   
    * --max_predictions_per_seq=20   
    * --masked_lm_prob=0.15   
    * --random_seed=12345   
    * --dupe_factor=5
3. run pretraining.py:
    * python run_pretraining.py \
    * --input_file=./tmp/tf_examples.tfrecord \
    * --output_dir=./tmp/pretraining_output \
    * --do_train=True \
    * --do_eval=True \
    * --bert_config_file=./pretrained/uncased_L-12_H-768_A-12/bert_config.json \
    * --init_checkpoint=./pretrained/uncased_L-12_H-768_A-12/bert_model.ckpt \
    * --train_batch_size=32 \
    * --max_seq_length=128 \
    * --max_predictions_per_seq=20 \
    * --num_train_steps=20 \
    * --num_warmup_steps=10 \
    * --learning_rate=2e-5

In [28]:
import tensorflow as tf
from google.protobuf.json_format import MessageToJson
import json
from pandas.io.json import json_normalize
import pandas as pd
import re

count=0
for example in tf.python_io.tf_record_iterator("tmp/tf_examples.tfrecord"):
    result =MessageToJson(tf.train.Example.FromString(example),preserving_proto_field_name=True)
    j_result=json.loads(result)
    count += 1
    print('Record:',count,'**************')

    print('input_ids: ',(j_result["features"]["feature"]['input_ids']['int64_list']['value']))
    print('input_mask: ',(j_result["features"]["feature"]['input_mask']['int64_list']['value']))
    print('segment_ids: ',(j_result["features"]["feature"]['segment_ids']['int64_list']['value']))
    print('next_sentence_labels: ',(j_result["features"]["feature"]['next_sentence_labels']['int64_list']['value']))
    print('masked_lm_positions: ',(j_result["features"]["feature"]['masked_lm_positions']['int64_list']['value']))
    print('masked_lm_ids: ',(j_result["features"]["feature"]['masked_lm_ids']['int64_list']['value']))
    print('masked_lm_weights: ',(j_result["features"]["feature"]['masked_lm_weights']['float_list']['value']))
   
    

Record: 1 **************
input_ids:  ['101', '2005', '2062', '2084', '1037', '103', '2039', '103', '2307', '2364', '2395', '1010', '103', '103', '103', '2803', '1997', '1996', '2103', '1010', '2012', '2157', '12113', '1010', '103', '2028', '8053', '12047', '1010', '2012', '2169', '2203', '30250', '2029', '1010', '2661', '2185', '1010', '2596', '1010', '11737', '1998', '6802', '2058', '1996', '4641', '1997', '1996', '2542', '5460', '1997', '5467', '1010', '1996', '3756', '103', '1011', '4564', '1997', '103', '103', '1025', '2096', '2012', '1996', '2203', '1997', '1996', '13005', '1999', '2392', '103', '2068', '25224', '1996', '2630', '7440', '1010', '2083', '1037', '2897', '102', '4298', '2023', '2089', '2031', '2042', '1996', '3114', '2339', '2220', '4125', '2869', '1999', '103', '10246', '1010', '2076', '1996', '16373', '2161', '1010', '4233', '103', '103', '103', '1997', '2303', '1010', '1998', '15839', '4196', '103', '2159', '103', '1996', '16931', '103', '2030', '2634', '1011', '10

Record: 57 **************
input_ids:  ['101', '1996', '11772', '2013', '103', '3536', '8632', '4188', '2000', '2785', '2571', '29326', '2543', '2000', '4318', '2010', '2793', '1011', '4253', '1010', '1998', '2002', '103', '28667', '22957', '2063', '2000', '103', '2062', '3073', '103', '11429', '1005', '1055', '2000', '4425', '1996', '18888', '1012', '2023', '2001', '3053', '4500', '1012', '2720', '1012', '16220', '103', '4625', '1996', '3307', '1010', '1998', '103', '3402', '1012', '102', '2077', '2032', '1012', '2751', '1010', '7543', '999', '2021', '1010', '6919', '103', '14396', '1010', '2025', '103', '12052', '103', '4338', '3238', '15778', '1997', '13587', '10848', '1010', '4840', '2013', '3267', '1005', '1055', '103', '13963', '1010', '2021', '1037', '2978', '1997', '13713', '2121', '1005', '1055', '2192', '2594', '27528', '2102', '1999', '1996', '2433', '1997', '1037', '5810', '103', '3614', '1012', '2559', '2012', '103', '2062', '2012', '103', '25499', '1010', '2002', '2387', '

#### the  example file pre training results:  (file: eval_results.txt)
    global_step = 20
    loss = 0.35513553
    masked_lm_accuracy = 0.9367975
    masked_lm_loss = 0.35329777
    next_sentence_accuracy = 1.0
    next_sentence_loss = 0.0006266979
    
####  base model all trainable parameters:  
    
        * word_embeddings:0, shape = (30522, 768) 
        * token_type_embeddings:0, shape = (2, 768) 
        * position_embeddings:0, shape = (512, 768) 
        * LayerNorm/beta:0, shape = (768,) 
        * LayerNorm/gamma:0, shape = (768,) 

        attention layers (all * 12 layers):
            * query/kernel:0, shape = (768, 768)
            * query/bias:0, shape = (768,)

            * key/kernel:0, shape = (768, 768)
            * key/bias:0, shape = (768,)

            * value/kernel:0, shape = (768, 768)
            * value/bias:0, shape = (768,)

            * output/dense/kernel:0, shape = (768, 768)
            * output/dense/bias:0, shape = (768,)

            * LayerNorm/beta:0, shape = (768,)
            * output/LayerNorm/gamma:0, shape = (768,)

            * intermediate/dense/kernel:0, shape = (768, 3072)
            * intermediate/dense/bias:0, shape = (3072,)

            * output/dense/kernel:0, shape = (3072, 768)
            * output/dense/bias:0, shape = (768,)

            * output/LayerNorm/beta:0, shape = (768,)
            * output/LayerNorm/gamma:0, shape = (768,)

        * pooler/dense/kernel:0, shape = (768, 768)
        * pooler/dense/bias:0, shape = (768,)

        * dense/kernel:0, shape = (768, 768)
        * dense/bias:0, shape = (768,)

        * LayerNorm/beta:0, shape = (768,)
        * LayerNorm/gamma:0, shape = (768,)

        * output_bias:0, shape = (30522,)
        * output_weights:0, shape = (2, 768)
        * output_bias:0, shape = (2,) 
        
        

### Pretraining top level pseudo-code(Estimator API) (both train and eval):

 main ()
 
    {
     //get configuration
     bert_config = modeling.BertConfig.from_json_file(FLAGS.bert_config_file)  
     
     //if use Cloud TPU
     run_config = tf.contrib.tpu.RunConfig(...) 
    
     //data are stored as tfrecords in files, here we populate a list of files with glob pattern.
     input_files = []
     for input_pattern in FLAGS.input_file.split(","):
        input_files.extend(tf.gfile.Glob(input_pattern))
    
      //build a model_fn with a builder closure function
      model_fn = model_fn_builder(...)
     
      //create a estimtor with model_fn, 
      //TPUEstimator automatically revert to GPU and CPU estimator if TPU is not used.
      estimator = tf.contrib.tpu.TPUEstimator( ... model_fn ...)
     
      //training
      if FLAGS.do_train:
        //build a input function with a builder closure function
        train_input_fn = input_fn_builder( input_files=input_files, ...)
        
        //do training:
        estimator.train(input_fn=train_input_fn, max_steps=FLAGS.num_train_steps)
    
      //Eval
      if FLAGS.do_eval:
        //build a input function with a builder closure function
        eval_input_fn = input_fn_builder(input_files=input_files, ...)
        
        //do evalution:
        result = estimator.evaluate(input_fn=eval_input_fn, steps=FLAGS.max_eval_steps)

        
        //log evaul results:
        output_eval_file = os.path.join(FLAGS.output_dir, "eval_results.txt")
        with tf.gfile.GFile(output_eval_file, "w") as writer:
            tf.logging.info("***** Eval results *****")
            for key in sorted(result.keys()):
            tf.logging.info("  %s = %s", key, str(result[key]))
            writer.write("%s = %s\n" % (key, str(result[key])))
    }
    
  
  ### model_fn_builder closure function:
  
  def model_fn_builder(bert_config, init_checkpoint, learning_rate,
                     num_train_steps, num_warmup_steps, use_tpu,
                     use_one_hot_embeddings):
    
    
      //this is the model function, it will be called by estimator
      //features, labels,mode, extra params will provided by estimator
      def model_fn(features, labels, mode, params):
           
        //get necesary features for model,
        input_ids = features["input_ids"]
        ...

        is_training = (mode == tf.estimator.ModeKeys.TRAIN)
        
        //builder the model
        model = modeling.BertModel( ...)

        //find losses from model, inputs and labels
        //Here for BERT we have two tasks, so two losses
        (masked_lm_loss,
         masked_lm_example_loss, masked_lm_log_probs) = get_masked_lm_output(
             bert_config, model.get_sequence_output(), model.get_embedding_table(),
             masked_lm_positions, masked_lm_ids, masked_lm_weights)

        
        (next_sentence_loss, next_sentence_example_loss,
         next_sentence_log_probs) = get_next_sentence_output(
             bert_config, model.get_pooled_output(), next_sentence_labels)

        //
        total_loss = masked_lm_loss + next_sentence_loss

        tvars = tf.trainable_variables()

        initialized_variable_names = {}
        scaffold_fn = None
        
        //load pretrain model or previous checkpoint
        if init_checkpoint:
        
          //get variables assignmen map
          (assignment_map, initialized_variable_names
          ) = modeling.get_assignment_map_from_checkpoint(tvars, init_checkpoint)
          
          if use_tpu:  // a tpu scaffold function is needed
          
            def tpu_scaffold():  //why use closure here? 
              tf.train.init_from_checkpoint(init_checkpoint, assignment_map)
              return tf.train.Scaffold()

            scaffold_fn = tpu_scaffold
          else:
            tf.train.init_from_checkpoint(init_checkpoint, assignment_map)
 

        //define estimator output_spec
        output_spec = None
        
        //for train phase:
        if mode == tf.estimator.ModeKeys.TRAIN:
          
          //create a optimizer and get train_op
          train_op = optimization.create_optimizer(
              total_loss, learning_rate, num_train_steps, num_warmup_steps, use_tpu)
          
          //hook up loss,train_op to estimator by defining a estimator output spec as return of the model_fn.
          output_spec = tf.contrib.tpu.TPUEstimatorSpec(
              mode=mode,
              loss=total_loss,
              train_op=train_op,
              scaffold_fn=scaffold_fn)
              
        //for eval phase:
        elif mode == tf.estimator.ModeKeys.EVAL:
          //needs a metric_fn closure to provide detail metrics
          def metric_fn(...):
            """Computes the loss and accuracy of the model."""
             ....
            //return metrics detail
            return {
                "masked_lm_accuracy": masked_lm_accuracy,
                "masked_lm_loss": masked_lm_mean_loss,
                "next_sentence_accuracy": next_sentence_accuracy,
                "next_sentence_loss": next_sentence_mean_loss,
            }
            
          //define thr metrics with the metric_fn and parameters to it
          eval_metrics = (metric_fn, [ ... ])
          output_spec = tf.contrib.tpu.TPUEstimatorSpec(
              mode=mode,
              loss=total_loss,
              eval_metrics=eval_metrics,
              scaffold_fn=scaffold_fn)
        else:
          raise ValueError("Only TRAIN and EVAL modes are supported: %s" % (mode))

        return output_spec

  return model_fn
  
  ### input_fn_builder closure function:
  
      //Creates an input_fn closure to be passed to TPUEstimator.
      def input_fn_builder(input_files,
                             max_seq_length,
                             max_predictions_per_seq,
                             is_training,
                             num_cpu_threads=4):
          
          //The actual input function
          def input_fn(params):
          
            batch_size = params["batch_size"]
            
            //define features
            name_to_features = {
                "input_ids":
                    tf.FixedLenFeature([max_seq_length], tf.int64),
                "input_mask":
                    tf.FixedLenFeature([max_seq_length], tf.int64),
                "segment_ids":
                    tf.FixedLenFeature([max_seq_length], tf.int64),
                "masked_lm_positions":
                    tf.FixedLenFeature([max_predictions_per_seq], tf.int64),
                "masked_lm_ids":
                    tf.FixedLenFeature([max_predictions_per_seq], tf.int64),
                "masked_lm_weights":
                    tf.FixedLenFeature([max_predictions_per_seq], tf.float32),
                "next_sentence_labels":
                    tf.FixedLenFeature([1], tf.int64),
            }

            # For training, we want a lot of parallel reading and shuffling.
            # For eval, we want no shuffling and parallel reading doesn't matter.
            
            //from_tensor_slices loads saved tensors like TFRecords in our case here 
            if is_training:
              //here d is a dataset of tf.constant of file names. 
              //all the parallelism here is not necessary in our case, we got only one file but good for other cases
              d = tf.data.Dataset.from_tensor_slices(tf.constant(input_files)) //create a dataset from file names
              d = d.repeat() // tells the dataset to repeat itself indefinitely
              d = d.shuffle(buffer_size=len(input_files))

              # `cycle_length` is the number of parallel files that get read.
              cycle_length = min(num_cpu_threads, len(input_files))

              # `sloppy` mode means that the interleaving is not exact. This adds
              # even more randomness to the training pipeline.
              
              //add some parallelism to speed up processing, but in our case there is only one file.
             
             //here d is a TFRecordDataset on the left and on the right it is dataset of file names.
              d = d.apply(
                  tf.contrib.data.parallel_interleave(
                      tf.data.TFRecordDataset,
                      sloppy=is_training,
                      cycle_length=cycle_length))
                      
              d = d.shuffle(buffer_size=100) //shuffle TFRecords
            else:
              d = tf.data.TFRecordDataset(input_files)
              # Since we evaluate for a fixed number of steps we don't want to encounter
              # out-of-range exceptions.
              d = d.repeat()

            # We must `drop_remainder` on training because the TPU requires fixed
            # size dimensions. For eval, we assume we are evaluating on the CPU or GPU
            # and we *don't* want to drop the remainder, otherwise we wont cover
            # every sample.
            
            //here we map the TFrecords to features and set up batches: _decode_record
            //_decode_record: use tf.parse_single_example to construct a dict mapping feature keys to Tensor values
            d = d.apply(
                tf.contrib.data.map_and_batch(
                    lambda record: _decode_record(record, name_to_features),
                    batch_size=batch_size,
                    num_parallel_batches=num_cpu_threads,
                    drop_remainder=True))
            return d

          return input_fn

### Fine tuning for target tasks example: application to Squad datasets (V1.1 and V2):  

Squad dataset data schema: answers for training has only one text, but evalution set(dev), it can have multiples.
    
    {'version': 'v2.0',
         'data': 
         [
          { 'title': 'Normans',
            'paragraphs': 
             [
               {'qas': 
                   [
                       { 'question': 'In what country is Normandy located?',
                         'id': '56ddde6b9a695914005b9628',
                         'answers': 
                             [
                                 {'text': 'France', 'answer_start': 159},
                                 {...}, 
                                    ...
                             ],
                          'is_impossible': False
                        },
                        {...},
                        ...
                  ],
               'context': '...'
               },
           
               { ...},
               
               ...
              ]
             },  
             
             { ...},
             
             ...
           ]
        }
    
    
### Squad task is a span prediction task, which find the best answer in the original text in form of a span of text. So the task predicts the best span start position and span ending position.  
        
      SQuAD V1.1 contains 100,000+ question-answer pairs on 500+ articles. V2.0 differs from the V1.1 by adding over 50,000 new, unanswerable questions written adversarially by crowdworkers to look similar to answerable ones.
       
       The implementation of BERT application to SQUAD is a rather similar process to BERT pretraining step.  Basically now we need to use the pretrained BERT model, define the new input features and loss specific to SQUAD task, then train the BERT model using SQAUD dataset -- this is the fine tuning.
       
### Notes on implementation details:
    1. How to deal with long paragraph: sliding window, make the label is contained a window of orignal doc.
    2. 

In [101]:
import json
from pandas.io.json import json_normalize
import pandas as pd
import re

data=json.load((open('datasets/squad/train-v2.0.json')))  #(open()) give up a generator)



In [102]:
#data['data'][0]['paragraphs'][0].keys()

for i in range(len(data['data'])):
    print('Title {}:'.format(i+1),data['data'][i]['title'],' has {} paragraphs'.format(len(data['data'][i]['paragraphs'])))
    for j in range(len(data['data'][i]['paragraphs'])):
        print ('    No. {} paragraph has {} QA sets'.format(j+1,len(data['data'][i]['paragraphs'][j]['qas'])))
        for k in range(len(data['data'][i]['paragraphs'][j]['qas'])):
            print('        No. {} question has {} answers.'.format(k+1,len(data['data'][i]['paragraphs'][j]['qas'][k]['answers'] )))
    

Title 1: Beyoncé  has 66 paragraphs
    No. 1 paragraph has 15 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 question has 1 answers.
        No. 10 question has 1 answers.
        No. 11 question has 1 answers.
        No. 12 question has 1 answers.
        No. 13 question has 1 answers.
        No. 14 question has 1 answers.
        No. 15 question has 1 answers.
    No. 2 paragraph has 12 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 

        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 question has 1 answers.
        No. 10 question has 1 answers.
    No. 27 paragraph has 15 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 question has 1 answers.
        No. 10 question has 1 answers.
        No. 11 question has 1 answers.
        No. 12 question has 1 answers.
        No. 13 question has 1 answers.
        No. 14 question has 1 answers.
        No. 15 question has 1 answers.
    No. 28 paragraph has 9 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No

        No. 8 question has 1 answers.
        No. 9 question has 1 answers.
    No. 28 paragraph has 3 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
    No. 29 paragraph has 3 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
    No. 30 paragraph has 4 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
    No. 31 paragraph has 7 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
    No. 32 paragraph has 6 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 

        No. 10 question has 0 answers.
    No. 33 paragraph has 7 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
    No. 34 paragraph has 11 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 0 answers.
        No. 9 question has 0 answers.
        No. 10 question has 0 answers.
        No. 11 question has 0 answers.
    No. 35 paragraph has 10 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 qu

        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
    No. 42 paragraph has 6 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
    No. 43 paragraph has 5 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
    No. 44 paragraph has 1 QA sets
        No. 1 question has 1 answers.
    No. 45 paragraph has 3 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question h

...

        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
    No. 73 paragraph has 5 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
    No. 74 paragraph has 5 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
    No. 75 paragraph has 5 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
    No. 76 paragraph has 4 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
    No. 77 paragraph has 5 QA sets
        No. 1 question has 

        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 0 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
        No. 9 question has 0 answers.
    No. 36 paragraph has 8 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
Title 430: Genocide  has 26 paragraphs
    No. 1 paragraph has 15 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
        No. 9 que

        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
        No. 9 question has 0 answers.
    No. 26 paragraph has 8 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
    No. 27 paragraph has 9 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 0 answers.
        No. 7 question has 0 answers.
        No. 8 question has 0 answers.
        No. 9 ques

        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 question has 1 answers.
        No. 10 question has 1 answers.
        No. 11 question has 1 answers.
        No. 12 question has 1 answers.
        No. 13 question has 1 answers.
        No. 14 question has 1 answers.
        No. 15 question has 0 answers.
        No. 16 question has 0 answers.
        No. 17 question has 0 answers.
        No. 18 question has 0 answers.
        No. 19 question has 0 answers.
    No. 2 paragraph has 13 QA sets
        No. 1 question has 1 answers.
        No. 2 question has 1 answers.
        No. 3 question has 1 answers.
        No. 4 question has 1 answers.
        No. 5 question has 1 answers.
        No. 6 question has 1 answers.
        No. 7 question has 1 answers.
        No. 8 question has 1 answers.
        No. 9 question has 0 answers.
        No. 10 question has 0 answers.
    

        No. 2 question has 0 answers.
        No. 3 question has 0 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
    No. 18 paragraph has 5 QA sets
        No. 1 question has 0 answers.
        No. 2 question has 0 answers.
        No. 3 question has 0 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
    No. 19 paragraph has 5 QA sets
        No. 1 question has 0 answers.
        No. 2 question has 0 answers.
        No. 3 question has 0 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
    No. 20 paragraph has 5 QA sets
        No. 1 question has 0 answers.
        No. 2 question has 0 answers.
        No. 3 question has 0 answers.
        No. 4 question has 0 answers.
        No. 5 question has 0 answers.
    No. 21 paragraph has 5 QA sets
        No. 1 question has 0 answers.
        No. 2 question has 0 answers.
        No. 3 question has 0 answers.
        No. 4 question h

In [103]:
qas=json_normalize(data['data'],['paragraphs','qas','answers'],[[ 'paragraphs','qas','is_impossible'],[ 'paragraphs','qas','question'],['paragraphs','context']])


In [131]:
#print(len(qas), len(qas[qas['is_impossible'==True]]))

len(qas[qas['text'] ==''])
len(qas)
#qas['paragraphs.qas.is_impossible']

86821

In [115]:
qas['q_first_word']=qas['paragraphs.qas.question'].str.lower().str.extract(r'^((?:\S+\s+){1}).*')

/Users/wweschen/venv/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: currently extract(expand=None) means expand=False (return Index/Series/DataFrame) but in a future version of pandas this will be changed to expand=True (return DataFrame)
  """Entry point for launching an IPython kernel.


In [116]:
qas.groupby('q_first_word').count().sort_values(by='text',ascending=False).head(30)

answer_start   text  paragraphs.qas.is_impossible  \
q_first_word                                                      
what                 37190  37190                         37190   
who                   8062   8062                          8062   
how                   8051   8051                          8051   
when                  5397   5397                          5397   
in                    4314   4314                          4314   
which                 4109   4109                          4109   
where                 3260   3260                          3260   
the                   2296   2296                          2296   
why                   1195   1195                          1195   
on                     580    580                           580   
along                  579    579                           579   
during                 435    435                           435   
at                     343    343                           343   
a                      307    307                           307   
for                    295    295                           295   
according              290    290                           290   
to                     289    289                           289   
from                   281    281                           281   
by                     258    258                           258   
after                  246    246                           246   
whose                  200    200                           200   
what's                 198    198                           198   
is                     191    191                           191   
if                     176    176                           176   
with                   172    172                           172   
as                     167    167                           167   
besides                161    161                           161   
are                    160    160                           160   
did                    155    155                           155   
name                   144    144                           144   

              paragraphs.qas.question  paragraphs.context  q_first_two_words  
q_first_word                                                                  
what                            37190               37190              37190  
who                              8062                8062               8062  
how                              8051                8051               8051  
when                             5397                5397               5397  
in                               4314                4314               4314  
which                            4109                4109               4109  
where                            3260                3260               3260  
the                              2296                2296               2296  
why                              1195                1195               1195  
on                                580                 580                580  
along                             579                 579                579  
during                            435                 435                435  
at                                343                 343                343  
a                                 307                 307                307  
for                               295                 295                295  
according                         290                 290                290  
to                                289                 289                289  
from                              281                 281                281  
by                                258                 258                258  
after                             246                 246                246  
whose                             200                 200                200  
what's                            198               

In [110]:
#data['data'][0]
#qas.head()
qas['q_first_two_words']=qas['paragraphs.qas.question'].str.lower().str.extract(r'^((?:\S+\s+){1}\S+).*')

/Users/wweschen/venv/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: currently extract(expand=None) means expand=False (return Index/Series/DataFrame) but in a future version of pandas this will be changed to expand=True (return DataFrame)
  This is separate from the ipykernel package so we can avoid doing imports until


In [140]:
qas.groupby('q_first_two_words').count().sort_values(by='text',ascending=False).tail(300)

answer_start  text  paragraphs.qas.is_impossible  \
q_first_two_words                                                               
mustaqbal media                         1     1                             1   
mutts, dogs                             1     1                             1   
mutual funds                            1     1                             1   
mycetophilldae is                       1     1                             1   
myelin is                               1     1                             1   
mystic rabbi                            1     1                             1   
métal hurlant                           1     1                             1   
nagarjuna said                          1     1                             1   
namibia is                              1     1                             1   
nagarjuna's main                        1     1                             1   
nam the                                 1     1                             1   
name 3                                  1     1                             1   
name 6                                  1     1                             1   
name examples                           1     1                             1   
name four                               1     1                             1   
name madonna's                          1     1                             1   
name michigan's                         1     1                             1   
name philidelphia's                     1     1                             1   
name uk                                 1     1                             1   
musical genres                          1     1                             1   
musical forms                           1     1                             1   
music without                           1     1                             1   
music theorist                          1     1                             1   
mount damavand                          1     1                             1   
movements were                          1     1                             1   
mp3 files                               1     1                             1   
mp3gain is                              1     1                             1   
mrigavyadha destroys                    1     1                             1   
mrigavyadha means                       1     1                             1   
mrs. dubose                             1     1                             1   
...                                   ...   ...                           ...   
outside england,                        1     1                             1   
outside europe,                         1     1                             1   
over 90%                                1     1                             1   
over approximately                      1     1                             1   
orlam clans                             1     1                             1   
originally, how                         1     1                             1   
originally reservations                 1     1                             1   
originally alphabets                    1     1                             1   
only one                                1     1                             1   
only who                                1     1                             1   
ontological theory                      1     1                             1   
op. 74                                  1     1                             1   
opera began                             1     1                             1   
opera focused                           1     1                             1   
opera is                                1     1                             1   
opera was                               1     1                             1   
oppidan residences                      1     1             

In [138]:
qas.groupby('q_first_word').head(2).sort_values(by='q_first_word',ascending=True)

answer_start                                               text  \
69474           455                                               1887   
99               37                           Independent Women Part I   
68704            91  a separate set of cables or a chain attached t...   
68703             0    Elevators with more than 30 m (98 ft) of travel   
51268           195                                          to decide   
4954            654                                  pratītyasamutpāda   
34186           191                           Pharmaceutical companies   
55617           393                     "civilized" and "uncivilized."   
19370           142                                       To the south   
4758             59                                The College Dropout   
28075           163                                             Marian   
19354           366                                         the Levant   
36702           105                                              north   
17366            80                                         Josip Broz   
19371            53                                       In the north   
19369            53                                       In the north   
26884           584                                      The Yardbirds   
22576           548                                             943 mb   
133            1042                                    Luther Vandross   
2379            202                                 For Your Eyes Only   
86480           196                                     assist hunters   
36906           356                                           boomhuis   
12008           287                            Rice University Stadium   
528             154                                             People   
3433            298                                    Lower East Side   
16155            39                                       Proto-Slavic   
18004          1126                                             Punica   
12744           165                                    Western Catalan   
54433           257                                                USB   
23445           383                               Chihuahua and Parral   
...             ...                                                ...   
64239           319                                            Hungary   
7027             44                             condemned the protests   
16308           145                                     Uralic peoples   
50594           273                                      Yale Cabaret.   
50481           827                                               1968   
80640           115                    Grand Prince of the Kievan Rus'   
38201           253                                   derivative works   
81297            65                              outside their website   
81268           434                                              third   
81350             0                                             Google   
17228           243                      Alfredo Stroessner's Paraguay   
65991           133                                         embroidery   
79085           109                                              India   
5215             46                                               seon   
5218            369                                          spiritual   
79016           474                                                3 V   
58141            70  from the bottom up in an ordered succession of...   
38763           226                                               Hera   
36109          1163                                              Ammon   
19747           306                                              eight   
14765           534                      in the city centre, Xinjiekou   
63440             0                                The Charaka Samhita   
63472      